## Trace Dates guided by Category keywords

 * collected all the OCR texts
 * gather all text files in 1974 folder
 * check for keywords and keep track of file names
 * create folder with .key and .txt file names Annif ML training
 
 ### Outputs
 
 1. Extracts dates within texts into a .tsv file for each of the years
 * Generates similar .tsv file with count of "date" citations or references
 * Combines the 5 TSV files with date references into one

In [1]:
import os
import sys
import glob
from pathlib import Path
from pprint import pprint
import math
import re
from collections import Counter

current_directory = os.getcwd()
prj_root = os.path.dirname(current_directory)
data_dir = f'{prj_root}/data'
txt_xml_dir = f'{prj_root}/data/TXT_PROC'

proc_year = "1978"
path_list = []
for f in sorted(Path(txt_xml_dir).glob(f'{proc_year}/*.txt')):
    txt_path = str(f) # cast PosixPath to str
    txt_name = os.path.basename(txt_path)
    txt_sans_ext = os.path.splitext(txt_name)[0]
    path_list.append(txt_name)

    # xml_text_path = os.path.join(final_directory, '{}.xml'.format(txt_sans_ext))
    
# strip the newline character
path_list = [x.strip() for x in path_list]
pprint(path_list[0:10], indent=2)

[ 'dds-90325-page-8-article-01.txt',
  'dds-90325-page-8-article-03.txt',
  'dds-90325-page-8-article-05.txt',
  'dds-90325-page-8-article-06.txt',
  'dds-90325-page-8-article-08.txt',
  'dds-90325-page-8-article-10.txt',
  'dds-90325-page-8-article-12.txt',
  'dds-90325-page-8-article-13.txt',
  'dds-90325-page-8-article-14.txt',
  'dds-90325-page-8-article-15.txt']


### Extract correspondence

Identify keywords from common words used by readers in their letters. The keywords are classified into five top-level tags or letter categories. Each set of keywords maps to a single tag. The five tags were editor, editorial, article, comment, misc.

**editor** - mentions or addresses the editor in the correspondence  
**editorial** - refers to an earlier editorial  
**article** - mentions or refers to an article  
**comment** - used identify correspondences to other letters as opposed to editorials and newspaper articles  
**misc** - This comprised other common words such as name of the newspaper and refrains such as "allow me space   ..."

NB: These tags were not a subject vocabulary in the strict sense as much as they were text category.

In [2]:
keyword_sets = [
    # editor
    ["editor"], 
    # editorial
    ["editorial"], 
    # article
    ["article", "reporter"], 
    # comment
    ["correspond", "correspondent", "correspondence", "comment", "reply", "comments in", 
    "column", "mailbox", "issue", "issue of", 
    "paper appearing", "appeared", "appearing",
    "referring to the", "letter", "a letter", 
    "letter by", "letter headed", "written",   
    "daily nation reader",
    "support", "suggested by", "referring to"],
    # misc
    ["daily", "nation", "your paper", "space"]]

vocabrefs = ["editor", "editorial", "article", "comment", "misc"]

In [3]:
import nltk
from collections import Counter
from shutil import copyfile
import pandas as pd

found_count = 0
total_valid_letters = 0
extracted_dates = []
for idx, path in enumerate(path_list):
    print(f'------++++++++++++==================== BEGIN {path} ================++++++++++------')
    total_matched_words = 0
    matched_words = {}
    vocabs = ''
    found_tokens = []
    
    txt_name = os.path.basename(path)
    txt_sans_ext = os.path.splitext(txt_name)[0]
    with open(f"{txt_xml_dir}/{proc_year}/{path}", 'r', encoding='utf-8') as infile:
        file_text = infile.read()

        word_tokens_nltk = nltk.word_tokenize(file_text)
        
        for idxx, vocabterms in enumerate(keyword_sets):  # Goes through the tokens in the list
            
            num_target_words = 0
            for idxxx, keytoken in enumerate(vocabterms):
                # match strictly whole words only
                found_what = [m.group(1) for l in word_tokens_nltk for m in [re.search(f'.*(\\b{keytoken}\\b).*', l)] if m]
                re.purge()               
                if found_what:  # For each one it checks if it is in the target list
                    total_matched_words += 1                  
                    num_target_words += len(found_what)                  
                    ref = vocabrefs[idxx]  # assign ref based on the current vocabset in the loop
                    # print(found_what, len(found_what), num_target_words, ref)                    
                    matched_words.update({ref: num_target_words})
                    found_tokens.append(ref)

        # remove duplicates and sort by the most frequent as top subject
        found_tokens = [key for key, value in Counter(found_tokens).most_common()]
        vocabs = '\n'.join(found_tokens)
        
        if total_matched_words >= 2:
            # https://stackoverflow.com/a/2655512/754432
            dates = []
            for date_like in re.findall(r'\b(?:jan(?:uary)?|feb(?:ruary)?|mar(?:ch)?|apr(?:il)?|may|jun(?:e)?|jul(?:y)?|aug(?:ust)?|sep(?:tember)?|nov(?:ember)?|dec(?:ember)?)(?:.{0,1}) (?:\d{1}|\d{2})(?=\D|$)', file_text):
                dates.append(date_like)
                
            ref_list = []
            for ref in vocabrefs:
                if ref in matched_words.keys():
                    ref_list.append(matched_words[ref])
                else:
                    ref_list.append(0)

            if len(dates) > 0:
                found_count += 1
                extracted_dates.append([path, dates, *ref_list])
            
            total_valid_letters += 1
            pprint(ref_list, indent=2)
            pprint(matched_words, indent=2)
            pprint(extracted_dates, indent=2)
            print(sum(matched_words.values()), len(matched_words), dates, path)

        # text_obj = nltk.Text(lower_case_tokens)
        # text_obj.concordance("letter", width=100)

print("Matches", total_valid_letters, "Found count", found_count)

------++++++++++++==================== BEGIN dds-90325-page-8-article-01.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90325-page-8-article-03.txt ================++++++++++------
[0, 0, 0, 2, 0]
{'comment': 2}
[['dds-90325-page-8-article-03.txt', ['september 22'], 0, 0, 0, 2, 0]]
2 1 ['september 22'] dds-90325-page-8-article-03.txt
------++++++++++++==================== BEGIN dds-90325-page-8-article-05.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90325-page-8-article-06.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90325-page-8-article-08.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90325-page-8-article-10.txt ================++++++++++------
[0, 0, 0, 2, 5]
{'comment': 2, 'misc': 5}
[['dds-90325-page-8-article-03.txt', ['september 22'], 0, 0, 0, 2, 0]]
7 2 [] dds-90325-page-8-article-10.txt
------++++++++++++===============

[0, 0, 0, 4, 1]
{'comment': 4, 'misc': 1}
[ ['dds-90325-page-8-article-03.txt', ['september 22'], 0, 0, 0, 2, 0],
  ['dds-90326-page-8-article-21.txt', ['december 23'], 0, 0, 0, 4, 0],
  ['dds-90328-page-8-article-10.txt', ['december 11'], 3, 2, 0, 0, 1],
  [ 'dds-90329-page-8-article-07.txt',
    ['december 23', 'december 14'],
    0,
    0,
    0,
    4,
    1]]
5 2 ['december 23', 'december 14'] dds-90329-page-8-article-07.txt
------++++++++++++==================== BEGIN dds-90329-page-8-article-10.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90329-page-8-article-12.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90329-page-8-article-13.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90329-page-8-article-15.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90329-page-8-article-19.txt ================++++++++++------
------++++++++++

[0, 0, 0, 3, 1]
{'comment': 3, 'misc': 1}
[ ['dds-90325-page-8-article-03.txt', ['september 22'], 0, 0, 0, 2, 0],
  ['dds-90326-page-8-article-21.txt', ['december 23'], 0, 0, 0, 4, 0],
  ['dds-90328-page-8-article-10.txt', ['december 11'], 3, 2, 0, 0, 1],
  [ 'dds-90329-page-8-article-07.txt',
    ['december 23', 'december 14'],
    0,
    0,
    0,
    4,
    1],
  ['dds-90332-page-8-article-25.txt', ['may 1'], 0, 0, 0, 3, 1]]
4 2 ['may 1'] dds-90332-page-8-article-25.txt
------++++++++++++==================== BEGIN dds-90332-page-8-article-26.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90333-page-8-article-01.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90333-page-8-article-06.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90333-page-8-article-07.txt ================++++++++++------
------++++++++++++==================== BEGIN dds-90333-page-8-article-08.txt =====

------++++++++++++==================== BEGIN dds-90337-page-8-article-00.txt ================++++++++++------
[0, 0, 1, 3, 2]
{'article': 1, 'comment': 3, 'misc': 2}
[ ['dds-90325-page-8-article-03.txt', ['september 22'], 0, 0, 0, 2, 0],
  ['dds-90326-page-8-article-21.txt', ['december 23'], 0, 0, 0, 4, 0],
  ['dds-90328-page-8-article-10.txt', ['december 11'], 3, 2, 0, 0, 1],
  [ 'dds-90329-page-8-article-07.txt',
    ['december 23', 'december 14'],
    0,
    0,
    0,
    4,
    1],
  ['dds-90332-page-8-article-25.txt', ['may 1'], 0, 0, 0, 3, 1],
  ['dds-90334-page-8-article-07.txt', ['september 17'], 0, 0, 0, 1, 1],
  ['dds-90334-page-8-article-14.txt', ['january 11'], 0, 0, 1, 2, 0],
  ['dds-90336-page-8-article-18.txt', ['january 10'], 1, 0, 0, 1, 1]]
6 3 [] dds-90337-page-8-article-00.txt
------++++++++++++==================== BEGIN dds-90337-page-8-article-03.txt ================++++++++++------
[0, 0, 1, 3, 2]
{'article': 1, 'comment': 3, 'misc': 2}
[ ['dds-90325-page-8-articl

    0,
    0,
    0,
    4,
    1],
  ['dds-90332-page-8-article-25.txt', ['may 1'], 0, 0, 0, 3, 1],
  ['dds-90334-page-8-article-07.txt', ['september 17'], 0, 0, 0, 1, 1],
  ['dds-90334-page-8-article-14.txt', ['january 11'], 0, 0, 1, 2, 0],
  ['dds-90336-page-8-article-18.txt', ['january 10'], 1, 0, 0, 1, 1],
  ['dds-90338-page-8-article-09.txt', ['january 14'], 0, 0, 0, 2, 2],
  ['dds-90338-page-8-article-13.txt', ['january 10'], 0, 0, 0, 1, 1],
  ['dds-90339-page-8-article-08.txt', ['january 5'], 0, 0, 0, 2, 2]]
4 2 ['january 5'] dds-90339-page-8-article-08.txt
------++++++++++++==================== BEGIN dds-90339-page-8-article-10.txt ================++++++++++------
[0, 0, 0, 2, 0]
{'comment': 2}
[ ['dds-90325-page-8-article-03.txt', ['september 22'], 0, 0, 0, 2, 0],
  ['dds-90326-page-8-article-21.txt', ['december 23'], 0, 0, 0, 4, 0],
  ['dds-90328-page-8-article-10.txt', ['december 11'], 3, 2, 0, 0, 1],
  [ 'dds-90329-page-8-article-07.txt',
    ['december 23', 'december 14']

...

  ['dds-90409-page-8-article-19.txt', ['april 3'], 0, 1, 0, 0, 1],
  ['dds-90410-page-8-article-14.txt', ['april 7'], 0, 0, 0, 1, 2],
  ['dds-90413-page-8-article-08.txt', ['april 5'], 0, 0, 0, 3, 2],
  ['dds-90418-page-8-article-03.txt', ['april 19'], 0, 0, 0, 5, 1],
  ['dds-90419-page-8-article-01.txt', ['april 19', 'april 7'], 0, 1, 0, 7, 0],
  ['dds-90420-page-8-article-01.txt', ['april 11'], 0, 1, 0, 1, 0],
  ['dds-90421-page-8-article-15.txt', ['april 27'], 0, 0, 0, 0, 2],
  ['dds-90422-page-8-article-01.txt', ['april 11'], 0, 0, 0, 2, 2],
  ['dds-90422-page-8-article-02.txt', ['april 19'], 0, 0, 0, 1, 2],
  ['dds-90422-page-8-article-08.txt', ['april 21'], 0, 0, 0, 0, 2],
  ['dds-90423-page-8-article-03.txt', ['april 15'], 1, 1, 0, 3, 0],
  ['dds-90425-page-8-article-07.txt', ['april 13'], 0, 0, 0, 1, 2],
  ['dds-90425-page-8-article-11.txt', ['april. 18'], 0, 0, 0, 2, 0],
  ['dds-90427-page-8-article-14.txt', ['april 24', 'april 28'], 0, 0, 0, 4, 2],
  ['dds-90432-page-8-articl

    1,
    0,
    0,
    1],
  ['dds-90531-page-8-article-00.txt', ['september 22'], 1, 0, 0, 4, 3],
  ['dds-90531-page-8-article-07.txt', ['september’ 21'], 0, 0, 1, 1, 1],
  ['dds-90531-page-8-article-10.txt', ['september 19'], 0, 2, 0, 2, 0],
  ['dds-90532-page-8-article-01.txt', ['september 20'], 0, 0, 0, 6, 1],
  ['dds-90533-page-8-article-01.txt', ['september 20'], 0, 0, 0, 5, 1],
  [ 'dds-90536-page-8-article-04.txt',
    ['september 24', 'september 24'],
    0,
    0,
    0,
    1,
    2],
  ['dds-90538-page-8-article-08.txt', ['september 22'], 0, 0, 0, 1, 1],
  ['dds-90538-page-8-article-15.txt', ['september 30'], 0, 0, 0, 3, 0],
  ['dds-90541-page-8-article-22.txt', ['september. 27'], 0, 0, 1, 0, 1],
  ['dds-90543-page-8-article-19.txt', ['september 27'], 0, 0, 0, 3, 1],
  ['dds-90547-page-8-article-27.txt', ['september 15'], 0, 0, 1, 0, 1],
  ['dds-90550-page-8-article-06.txt', ['august 16'], 0, 0, 0, 2, 1],
  ['dds-90564-page-8-article-19.txt', ['november 4'], 0, 0, 0, 1, 2

  ['dds-90404-page-8-article-15.txt', ['april 5'], 0, 0, 0, 3, 0],
  ['dds-90409-page-8-article-19.txt', ['april 3'], 0, 1, 0, 0, 1],
  ['dds-90410-page-8-article-14.txt', ['april 7'], 0, 0, 0, 1, 2],
  ['dds-90413-page-8-article-08.txt', ['april 5'], 0, 0, 0, 3, 2],
  ['dds-90418-page-8-article-03.txt', ['april 19'], 0, 0, 0, 5, 1],
  ['dds-90419-page-8-article-01.txt', ['april 19', 'april 7'], 0, 1, 0, 7, 0],
  ['dds-90420-page-8-article-01.txt', ['april 11'], 0, 1, 0, 1, 0],
  ['dds-90421-page-8-article-15.txt', ['april 27'], 0, 0, 0, 0, 2],
  ['dds-90422-page-8-article-01.txt', ['april 11'], 0, 0, 0, 2, 2],
  ['dds-90422-page-8-article-02.txt', ['april 19'], 0, 0, 0, 1, 2],
  ['dds-90422-page-8-article-08.txt', ['april 21'], 0, 0, 0, 0, 2],
  ['dds-90423-page-8-article-03.txt', ['april 15'], 1, 1, 0, 3, 0],
  ['dds-90425-page-8-article-07.txt', ['april 13'], 0, 0, 0, 1, 2],
  ['dds-90425-page-8-article-11.txt', ['april. 18'], 0, 0, 0, 2, 0],
  ['dds-90427-page-8-article-14.txt', ['

  ['dds-90396-page-8-article-07.txt', ['march 7'], 0, 0, 0, 1, 1],
  ['dds-90396-page-8-article-09.txt', ['march 26'], 0, 0, 0, 1, 1],
  ['dds-90396-page-8-article-22.txt', ['march 18'], 0, 0, 0, 2, 0],
  ['dds-90397-page-8-article-08.txt', ['march 22'], 0, 0, 0, 3, 0],
  ['dds-90397-page-8-article-12.txt', ['march 23'], 0, 0, 0, 3, 0],
  ['dds-90397-page-8-article-15.txt', ['march 19'], 1, 0, 0, 1, 2],
  ['dds-90398-page-8-article-06.txt', ['march 20', 'march 4'], 0, 0, 0, 2, 0],
  ['dds-90398-page-8-article-14.txt', ['march 18'], 0, 1, 0, 0, 1],
  ['dds-90399-page-8-article-06.txt', ['march 18'], 1, 1, 0, 1, 0],
  ['dds-90399-page-8-article-09.txt', ['march’ 9'], 0, 0, 0, 0, 2],
  [ 'dds-90399-page-8-article-11.txt',
    ['march 13', 'february 1'],
    0,
    0,
    0,
    0,
    2],
  ['dds-90402-page-8-article-24.txt', ['march 14'], 0, 0, 0, 2, 0],
  ['dds-90402-page-8-article-25.txt', ['march 14'], 0, 0, 0, 2, 0],
  ['dds-90404-page-8-article-13.txt', ['april 5'], 1, 0, 1, 0, 0],


  ['dds-90457-page-8-article-03.txt', ['june 3'], 1, 0, 0, 2, 2],
  ['dds-90463-page-8-article-01.txt', ['may 17', 'may 28'], 0, 0, 0, 3, 1],
  ['dds-90463-page-8-article-04.txt', ['june 13'], 0, 0, 0, 2, 0],
  ['dds-90463-page-8-article-07.txt', ['june 8'], 0, 0, 0, 1, 2],
  ['dds-90468-page-8-article-26.txt', ['june 17'], 0, 0, 0, 1, 1],
  ['dds-90471-page-8-article-15.txt', ['june 26'], 0, 0, 0, 0, 2],
  ['dds-90475-page-8-article-02.txt', ['june 20'], 0, 1, 0, 2, 1],
  ['dds-90475-page-8-article-08.txt', ['june 2'], 0, 1, 0, 1, 0],
  ['dds-90482-page-8-article-15.txt', ['july 10'], 1, 0, 0, 2, 2],
  ['dds-90486-page-8-article-21.txt', ['july 6'], 4, 0, 2, 0, 0],
  ['dds-90489-page-8-article-16.txt', ['june 24'], 0, 0, 0, 1, 1],
  ['dds-90490-page-8-article-16.txt', ['july 6'], 1, 1, 0, 0, 0],
  ['dds-90496-page-8-article-02.txt', ['july. 18'], 1, 0, 0, 1, 1],
  [ 'dds-90503-page-8-article-06.txt',
    ['january“ 10', 'january 6'],
    0,
    1,
    0,
    7,
    0],
  ['dds-90506-p

#### Process letters and extracted dates

Match article files with the list of column dates to proper assign dates for the dates extracted above

In [4]:
from datetime import datetime
import dateparser

data = pd.read_csv(f'{data_dir}/column_dates/{proc_year}.tsv', 
                   delimiter='\t', 
                   usecols=['page_image_name', 'cleaned_date'],
                   na_filter=False
                  )

dates_parsed = []
for index, row in data.iterrows():
    page_image_name = row['page_image_name']
    cleaned_date = row['cleaned_date']
    cleaned_datetime_obj = datetime.strptime(cleaned_date , '%Y-%m-%d')
    
    for extracted_date in extracted_dates:
        file_name = extracted_date[0]
        dates_list = extracted_date[1]
        
        editor = extracted_date[2]
        editorial = extracted_date[3]
        article = extracted_date[4]
        comment = extracted_date[5]
        misc = extracted_date[6]
        

        if file_name.startswith(page_image_name):
            # process date(s) in the file keeping in mind the date limit as barrier
            for ref_date in dates_list:
                datetime_inst = dateparser.parse(f"{ref_date} {proc_year}")
                if isinstance(datetime_inst, datetime):
                    # make year correct when its ahead of current date of the column
                    if datetime_inst > cleaned_datetime_obj:
                        datetime_inst = datetime_inst.replace(year=int(proc_year)-1) # make it last year

                    cleaned_date_obj = cleaned_datetime_obj.date()
                    date_inst = datetime_inst.date()
                    dates_parsed.append([
                        str(date_inst), 
                        str(cleaned_date_obj), 
                        file_name, 
                        editor, 
                        editorial, 
                        article, 
                        comment, 
                        misc
                    ])

# pprint(dates_parsed, indent=2)

In [5]:
headers = ['reference_date', 'letter_date', 'letter_filename', *vocabrefs]
new_data = pd.DataFrame(dates_parsed, columns=headers)

current_directory = os.getcwd()
prj_root = os.path.dirname(current_directory)
data_dir = f'{prj_root}/data'
files_and_dates_dir = f'{data_dir}/files_and_dates'

if not os.path.exists(files_and_dates_dir):
    os.makedirs(files_and_dates_dir)

processed_csv = os.path.join(files_and_dates_dir, f'{proc_year}.tsv')
new_data.to_csv(processed_csv, 
                sep='\t',
                encoding='utf-8', 
                index=False,
                columns = headers)

new_data.head(10)

reference_date letter_date                  letter_filename  editor  \
0     1977-09-22  1978-01-03  dds-90325-page-8-article-03.txt       0   
1     1977-12-23  1978-01-04  dds-90326-page-8-article-21.txt       0   
2     1977-12-11  1978-01-06  dds-90328-page-8-article-10.txt       3   
3     1977-12-23  1978-01-07  dds-90329-page-8-article-07.txt       0   
4     1977-12-14  1978-01-07  dds-90329-page-8-article-07.txt       0   
5     1977-05-01  1978-01-11  dds-90332-page-8-article-25.txt       0   
6     1977-09-17  1978-01-14  dds-90334-page-8-article-07.txt       0   
7     1978-01-11  1978-01-14  dds-90334-page-8-article-14.txt       0   
8     1978-01-10  1978-01-17  dds-90336-page-8-article-18.txt       1   
9     1978-01-14  1978-01-19  dds-90338-page-8-article-09.txt       0   

   editorial  article  comment  misc  
0          0        0        2     0  
1          0        0        4     0  
2          2        0        0     1  
3          0        0        4     1  
4          0        0        4     1  
5          0        0        3     1  
6          0        0        1     1  
7          0        1        2     0  
8          0        0        1     1  
9          0        0        2     2

## Merge all into one

Combined the 5 TSV files with date references into one

In [8]:
all_filenames = [i for i in sorted(glob.glob(f'{files_and_dates_dir}/[0-9][0-9][0-9][0-9].tsv'))]
pprint(all_filenames, indent=2)

# Step 3: Combine all files in the list and export as CSV
# Use pandas to concatenate all files in the list and export as CSV. The output file is named “combined_csv.csv” located in your working directory.

headers = ['reference_date', 'letter_date', 'letter_filename', *vocabrefs]
#combine all files in the list
combined_df = pd.concat([pd.read_csv(f,
                                      delimiter='\t', 
                                      usecols=headers,
                                      na_filter=False) for f in all_filenames]
                        )
#export to csv
combined_df.to_csv(f"{files_and_dates_dir}/combined.tsv", 
                    sep='\t',
                    index=False,
                    columns = headers,
                    encoding='utf-8')

[ '/home/anthony/Documents/UofA/Thesis/lettersiterate/data/files_and_dates/1974.tsv',
  '/home/anthony/Documents/UofA/Thesis/lettersiterate/data/files_and_dates/1975.tsv',
  '/home/anthony/Documents/UofA/Thesis/lettersiterate/data/files_and_dates/1976.tsv',
  '/home/anthony/Documents/UofA/Thesis/lettersiterate/data/files_and_dates/1977.tsv',
  '/home/anthony/Documents/UofA/Thesis/lettersiterate/data/files_and_dates/1978.tsv']


In [9]:
reference_counts = []
for index, row in combined_df.iterrows():
    reference_date = row['reference_date']
    letter_date = row['letter_date']
    letter_filename = row['letter_filename']
    editor = row['editor']
    editorial = row['editorial']
    article = row['article']
    comment = row['comment']
    misc = row['misc']
    ref_count = combined_df['reference_date'].eq(reference_date).sum()
    reference_counts.append([
        reference_date, 
        letter_date, 
        letter_filename, 
        ref_count,
        editor, 
        editorial, 
        article, 
        comment, 
        misc        
    ])

headers = ['reference_date', 'letter_date', 'letter_filename', 'ref_count', *vocabrefs]
combined_with_count_df = pd.DataFrame(reference_counts, columns=headers)

#export to tsv
combined_with_count_df.to_csv(f"{files_and_dates_dir}/combined_with_count.tsv", 
                    sep='\t',
                    index=False,
                    columns = headers,
                    encoding='utf-8')
    
# combined_df['letter_date'].value_counts()

In [ ]:
combined_df['reference_date'].value_counts()

In [ ]:
import dateparser

print(dateparser.parse("'december. 27'"))

In [ ]:
textt = "true picture  please refer to the letter “india is not. so poor” by mr. sudhir hendre, which appeared in the mailbox of july 18. having stayed in india for more than eight years, i highly appreciate the true picture of india given by mr. hendre.  the informations and the remedial suggestions given by him to change the misleading present knowledge about india is, i am sure, highly appreciated by all people concerned about the wellbeing and progress of india.  birendra patel, karantina."
textt = 'thrash out differences  allow me space in your paper to air my views about our church leaders at butare,  i highly support mr, banda daniels letter of december 17, 1974. it has become war between the “saved” people and the church leaders. as mr. banda quotes, the sayed people do conduct their prayers differently, they say they have climbed the ladder.  to my surprise, it is only at butare area. i would be very happy if the readers could tell me w. this sort of worship has come from. i would request the authority to convene a meeting between the “saved” people and the church leaders at butare to discuss the issue.  " odhtambo p. george, wehuye.'
textt = 'secretaries’ association.  i wish to comment on the letter from “miss secretary”. first of all i must mention that there was a lot of publicity after the men-. tinned association~ was formed for secretaries and after a few months of its existence, with no call for meetings, we thought it had dissolved! so it is still on? as this association does not appear. in the telephone directory we really got know where to contact you.  you mentioned a november 21 tea party which we attended and found nobody! i would also ‘like to mention that the way you have categorised memberships is most unfair. i have .80.40 shorthand and typing respectively. i have been working for the last 19 years as -a secretary. although i have not ‘attained the speeds needed to be a full member, i have the experience that those who hold the needed qualifications do not have.  you hold that you. want the junior secretary to work hard to attain the 100.40 speeds, but how do you really, define a junior secretary? as dictaphone take over, we feel speeds should come and place to experience? what do you say?  “executive seoretarion’, . jai  what people want to see'
# textt = 'let there he peace  before you close the correspond hence - now centered on on samba programmes and played thereon, i would be tek if  you grant me space in your paper % ada a few “paints to what my  predecessors, samba girl’ and “2nd disgusted kit girl” have ably pointed out, the ministry that vo isd ay going all it cam to cater for the needs of the wananchi, it is no secret that personnel who  prepare “and .release some of the vernacular programmes _ themselves ‘lack in the language flavour that~ goes for a good announcer. ha the samba’ programmes have sharply deteriorated and are. not what they were ‘during the heyday of people like combo, stephen kikuyu and john thau among others, ~. let us face it. what we want in samba programmes is the kind of music next to our hearts and not some wild concoctions as churned out. by’ sammy mbelenzi.. the variations in our music is wide and gives one a luscious field to choose .to there is no reason “ why we should be fed. fed with any other stuff apart from the real thing. we want to rest assured that we get the true worth of the 45 allocated, disgusted kamna”, nairobi. now  rae dana a'
textt = 'we are not equal  i wish to comment on the letter from a. rubia entitled “none of us is superior” nation. december 6. i agree that a man cannon survive without a woman, but this is not to say they are equals,  a woman is like a garden given to man by god. the duty of man jp to ensure that the garden is healthy so that he can plant his seeds and get another companion, a garden can have only one owner. if a man is dissatisfied with his garden, he can always buy another one,   the superiority of men is further strengthened by the fact that they are’ physically stronger — no woman can stand the blows of muhammad ali!  men are of. course more intelligent than women. the professors and makers of sophisticated things are men.-if the posts held by women in the government were. given to men, especially to school-weavers, the. economy of the country would still run smoothly.  what i want to stress is that there are more illiterate women than men. . .  ben a. aching, _ nairobi.'

import re
# re.findall('“([^”]*)”', textt)
# re.findall('\“(.+?)\”', textt)
re.findall('\“([^“]+?)\”', textt)
